# 2D to 3D LSTM

This is the first approach to try to estimate 3D points coordinates from 2D keypoints extracted with Openpose. Here I will build a simple LSTM to perform the task over the Panoptic Studio dataset.

First, let's import all the necessary libraries.

In [1]:
# Pytorch utilities
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader

from scipy.spatial.transform import Rotation as R

# Plotting utilities
%matplotlib widget
import matplotlib
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from IPython.display import HTML
import matplotlib.animation as animation
from torch.utils.tensorboard import SummaryWriter
from timeit import default_timer as timer
import pyprind

# Directory and file utilities
from os import listdir
from os.path import isfile, isdir, join
import json

## Notebook parameters

In [2]:
modes = { 0:'one video', 1:'one signer', 2:'all signers'}
MODE =  modes[0]
video = 7

## Data acquisition
Now I will define some functions in order to parse and organise the data, and later convert it to pytorch tensors.

The data is structured as follows: in the dataset directory there are several folders, each folder corresponds to a recording; each of these folders contains a folder with the audio, folders with face, hands and body keypoints estimations for each frame, and a folder with the video recorded from different views.

In this first approach I will be using the keypoints estimations. Every keypoint folder (face, hands or body) is organized the same way: it contains a json per frame of the video, which includes the 3D keypoints estimation.

The function `get_keypoints` will go through each folder in the dataset directory and retrieve the face keypoints, the hands keypoints and the body keypoints. It will separate them into input (2D coordinates per joint per frame) and grountruth (third coordinate to estimate for each input 2D keypoint). 
The input will be of shape $([n videos, seq len, input size])$, where *seq_len* = number of frames, and *input_size* = face + hands + body keypoints, that is (70+(21+21)+26)x2 -multiplied by 2 because there are x and y coordinates-. The groundtruth (label) data will be of the same shape, except that the last dimension size will not be multiplied by 2 (there's only one coordinate to estimate).  

In [3]:
def get_keypoints(data_path):
    dataset = []
    groundtruth = []
    # Look over just the folders inside the directory
    just_folders = filter(lambda x: isdir(join(data_path, x)), listdir(data_path))
    for p in list(map(lambda x: join(data_path, x), just_folders)): 
        # Gets 2 list of n_frames lists, one for the 2D coordinates and one for the third coordinate.
        # Each list of the n_frames lists contains, either the (x and y) or the z of each keypoint for the face(first line), hands(second), body(third).
        # e.g. the first line will result in [[x1,y1,x2,y2...x70,y70]sub1...[x1,y1...x70,y70]subN], [[z1,z2...z70]sub1...[z1..z70]subN]
        # Actually, as there will be two of each list above because there are two people en each video.
        face_2d, face_3d = get_face(p)
        hands_2d, hands_3d = get_hands(p)
        pose_2d, pose_3d = get_body(p)
        
        # Concatenates the coordinates for the face, hands and body on the last dimension, for each person.
        vid_input_p1, vid_input_p2 = ([fa+ha+po for fa, ha, po in zip(face_2d[i], hands_2d[i], pose_2d[i])] for i in range(2))
        vid_labels_p1, vid_labels_p2 = ([fa+ha+po for fa, ha, po in zip(face_3d[i], hands_3d[i], pose_3d[i])] for i in range(2))
        
        dataset.append(vid_input_p1)
        dataset.append(vid_input_p2)
        groundtruth.append(vid_labels_p1)
        groundtruth.append(vid_labels_p2)
        print(f'Completed folder {p}')
    return dataset, groundtruth

The following functions are in charge of retrieving the keypoints from each json. The json face json has a key *people* with a list of person objects. Each person object has *id* field and *landmarks* field, the latter containing a list of 3D coordinates for each keypoint.

In [4]:
def get_face(path):
    face_2D_seq = ([], [])
    face_3D_seq = ([], [])
    # List only the files (json), for there might be folders containing invalid frames.
    paths = map(lambda x: join(path, 'hdFace3d', x), sorted(listdir(join(path, 'hdFace3d'))))
    files = list(filter(lambda x: isfile(x), paths))
    for f in files: # The first frame of face keypoints estimation it's blank
        with open(f, 'r') as j:
            json_array = json.load(j)
            i = 0
            for person in json_array['people']:
                if person['id'] != -1: # If the id is -1, it means there's no person
                    x = person['face70']['landmarks'][::3]
                    y = person['face70']['landmarks'][1::3]
                    two_coord = [l[item] for item in range(len(x)) for l in [x,y]]
                    third_coord = person['face70']['landmarks'][2::3]
                    face_2D_seq[person['id']].append(two_coord)
                    face_3D_seq[person['id']].append(third_coord)
                    i+=1
                    pid = person['id']
            if i<2: # In case there was only one person detected on a frame
                face_2D_seq[1-pid].append(face_2D_seq[1-pid][-1])
                face_3D_seq[1-pid].append(face_3D_seq[1-pid][-1])
    print('Face completed.')
    # Each return var being a tuple with the list of n_frames list of coordinates for each person
    return face_2D_seq, face_3D_seq

The hands json contains the *landmarks* field inside both *left_hand* and *right_hand* field. As there are some frames that may not have one of the hands estimated, I've had to put some exception handling. 

In [5]:
def get_hands(path):
    hand_2D_seq = ([], [])
    hand_3D_seq = ([], [])
    paths = map(lambda x: join(path, 'hdHand3d', x), sorted(listdir(join(path, 'hdHand3d'))))
    files = list(filter(lambda x: isfile(x), paths))
    for f in files: # The first and the last frames of these folders are blank.
        with open(f, 'r') as j:
            json_array = json.load(j)
            i = 0
            for person in json_array['people']:
                if person['id'] != -1:
                    try:
                        # Separate x,y from z
                        hands= [[person[hand]['landmarks'][c] 
                                 for c in range(len(person['right_hand']['landmarks'])) if (c+1)%3!=0] 
                                 for hand in ['left_hand', 'right_hand']]
                        hand_2D_seq[person['id']].append(hands[0]+hands[1])
                        
                        hands_3d = [person[hand]['landmarks'][2::3] 
                                    for hand in ['left_hand', 'right_hand']]
                        hand_3D_seq[person['id']].append(hands_3d[0]+hands_3d[1])
                    
                    except Exception as e: # In case left_hand or right_hand keys don't exist.
                        if 'left_hand' in str(e): 
                            try: # Just put a 0., 0., 0. estimation for each keypoint of the left_hand
                                hands = hand_2D_seq[1-person['id']][-1][:42]+[person['right_hand']['landmarks'][c] 
                                                                 for c in range(len(person['right_hand']['landmarks'])) if (c+1)%3!=0]
                                hands_3d = hand_3D_seq[1-person['id']][-1][:21]+person['right_hand']['landmarks'][2::3]
                            except: # In case neither left_hand nor right_hand exist
                                hands = hand_2D_seq[1-person['id']][-1]
                                hands_3d = hand_3D_seq[1-person['id']][-1]
                        elif 'right_hand' in str(e): # Just put a 0., 0., 0. estimation for each keypoint of the right_hand
                            hands = [person['left_hand']['landmarks'][c] 
                                     for c in range(len(person['left_hand']['landmarks'])) if (c+1)%3!=0]+hand_2D_seq[1-person['id']][-1][42:]
                            hands_3d = person['left_hand']['landmarks'][2::3]+hand_3D_seq[1-person['id']][-1][21:]

                        hand_2D_seq[person['id']].append(hands)
                        hand_3D_seq[person['id']].append(hands_3d)
                    i+=1
                    pid = person['id']
            if i<2:
                hand_2D_seq[1-pid].append(hand_2D_seq[1-pid][-1])
                hand_3D_seq[1-pid].append(hand_3D_seq[1-pid][-1])
    print('Hands completed.')
    return hand_2D_seq, hand_3D_seq

The body json is organised a bit differently, inside each person object contains the *joints26* field with a list of 3D coordinates. But this list is structured as follows: *[x1,y1,z1,acc1,x2,y2,z2,acc2...]*.

In [6]:
def get_body(path):
    body_2D_seq = ([], [])
    body_3D_seq = ([], [])
    paths = map(lambda x: join(path, 'hdPose3d_stage1_op25', x), sorted(listdir(join(path, 'hdPose3d_stage1_op25'))))
    files = list(filter(lambda x: isfile(x), paths))
    for f in files:
        with open(f, 'r') as j:
            json_array = json.load(j)
            i = 0
            for person in json_array['bodies']:
                if person['id'] != -1:
                    x = person['joints26'][::4]
                    y = person['joints26'][1::4]
                    two_coord = [l[item] for item in range(len(x)) for l in [x,y]]
                    third_coord = person['joints26'][2::4]
                    body_2D_seq[person['id']].append(two_coord)
                    body_3D_seq[person['id']].append(third_coord)
                    i += 1
                    pid = person['id']
            if i<2:
                body_2D_seq[1-pid].append(body_2D_seq[1-pid][-1])
                body_3D_seq[1-pid].append(body_3D_seq[1-pid][-1])
    print('Body completed.')
    return body_2D_seq, body_3D_seq

In [7]:
data_path = '../../../data/DB keypoints'
dataset, groundtruth = get_keypoints(data_path)

FileNotFoundError: [Errno 2] No such file or directory: '../../../data/DB keypoints'

Add padding to shorter sequences and convert them to numpy arrays.

In [ ]:
def padding_seq(dataset):
    max_seq = max([len(x) for x in dataset])
    seq_lengths = []
    for seq in dataset:
        seq_lengths.append(len(seq))
        for i in range(max_seq-len(seq)):
            seq.append([np.nan for j in range(len(seq[0]))])
        
    return max_seq, seq_lengths

max_seq, seq_lengths = padding_seq(dataset)
_, _ = padding_seq(groundtruth)

In [ ]:
# From python lists to numpy ndarray.
dataset = np.asarray(dataset)
groundtruth = np.asarray(groundtruth)
lengths = np.asarray(seq_lengths)
print(dataset.shape, groundtruth.shape, lengths.shape)

Once they are numpy ndarrays I save the keypoints into pickle files for faster loading in later executions

In [10]:
np.save('../../pickles/dataset.npy', dataset)
np.save('../../pickles/groundtruth.npy', groundtruth)

In [11]:
np.save('../../pickles/lengths.npy', lengths)

## Dataset structuring
Now let's convert the lists obtained to Pytorch tensors and organise them in train, validation and test datasets. 
First, I will define a padding function in order to make all the sequences of video frames the same length, so I can train the LSTM in batches. 

#### Load from pickle
Load keypoints from pre-saved pickle files instead of directly reading the jsons.

In [3]:
dataset = np.load('../../pickles/dataset.npy', allow_pickle=True)
groundtruth = np.load('../../pickles/groundtruth.npy', allow_pickle=True)
lengths = np.load('../../pickles/lengths.npy', allow_pickle=True)
max_seq = dataset.shape[1]
print(max_seq)

8752


In [4]:
if MODE == 'one video':
    dataset, groundtruth = dataset[video], groundtruth[video]
    chunks_d = np.split(dataset, 547, axis=0)[:lengths[video]//16]
    chunks_g = np.split(groundtruth, 547, axis=0)[:lengths[video]//16]
    chunks_d = tuple(np.expand_dims(c, axis=0) for c in chunks_d)
    chunks_g = tuple(np.expand_dims(c, axis=0) for c in chunks_g)
    
    dataset = np.concatenate(chunks_d, axis=0)
    groundtruth = np.concatenate(chunks_g, axis=0)
    lengths = np.asarray([16 for i in range(lengths[video]//16)])
    print(lengths.shape)

elif MODE == 'one signer':
    dataset, groundtruth, lengths = dataset[20::2], groundtruth[20::2], lengths[20::2]
    print(lengths)
    chunks_d, chunks_g = np.split(dataset, 16, axis=1), np.split(groundtruth, 16, axis=1)
    
    dataset, groundtruth = np.concatenate(chunks_d, axis=0), np.concatenate(chunks_g, axis=0)
    lengths = np.concatenate(tuple([547 if j*547<=lengths[i] 
                                    else (lengths[i]%547 if (j-1)*547<lengths[i] 
                                          else 0) for i in range(12)] for j in range(1,17)), axis=0)
    print(dataset.shape, groundtruth.shape, lengths.shape)
    
elif MODE == 'all signers':
    chunks_d, chunks_g = np.split(dataset, 8, axis=1), np.split(groundtruth, 8, axis=1)
    
    dataset, groundtruth = np.concatenate(chunks_d, axis=0), np.concatenate(chunks_g, axis=0)
    lengths = np.concatenate(tuple([1094 if j*1094<=lengths[i] 
                                    else (lengths[i]%1094 if (j-1)*1094<lengths[i] 
                                          else 0) for i in range(44)] for j in range(1,9)), axis=0)
    print(dataset.shape, groundtruth.shape, lengths.shape)

(546,)


In [5]:
# Clean all NaN videos
dataset = np.delete(dataset, np.where(lengths==0), axis=0)
groundtruth = np.delete(groundtruth, np.where(lengths==0), axis=0)
lengths = np.delete(lengths, np.where(lengths==0), axis=0)

print(dataset.shape, groundtruth.shape, lengths.shape)

(546, 16, 276) (546, 16, 138) (546,)


For each axis I normalize the keypoints using the following formula:

In [6]:
def align(tensor, coordinates=1):
    for n_vid in range(tensor.shape[0]):
        max_value = [np.nanmax(tensor[n_vid, :,i::coordinates]) for i in range(coordinates)]
        min_value = [np.nanmin(tensor[n_vid, :,i::coordinates]) for i in range(coordinates)]
        center = [(max_value[i]+min_value[i])/2 for i in range(coordinates)]
        for j in range(coordinates):
            subtensor = tensor[n_vid, :, j::coordinates]
            subtensor[:] = np.subtract(subtensor, center[j])

align(dataset,2)
align(groundtruth)
print(dataset.shape, groundtruth.shape, lengths.shape)

(546, 16, 276) (546, 16, 138) (546,)


In [8]:
r = R.from_euler('y', 110, degrees=True)
shapes = dataset.shape
dataset = dataset.reshape(-1, 2)
groundtruth = groundtruth.reshape(-1,1)
xyz = np.concatenate((dataset, groundtruth), axis=1)
xyz = r.apply(xyz)
dataset, groundtruth = xyz[:, :2].reshape(shapes), xyz[:,2].reshape(shapes[0], shapes[1],138)

print(dataset.shape, groundtruth.shape)

(546, 16, 276) (546, 16, 138)


In [10]:
def norm_uniform(tensor, coordinates=1):
    scale = []
    for n_vid in range(tensor.shape[0]):
        coord_scale = []
        max_value = [np.nanmax(tensor[n_vid, :,i::coordinates]) for i in range(coordinates)]
        min_value = [np.nanmin(tensor[n_vid, :,i::coordinates]) for i in range(coordinates)]
        center = [(max_value[i]+min_value[i])/2 for i in range(coordinates)]
        for j in range(coordinates):
            subtensor = tensor[n_vid, :, j::coordinates]
            subtensor[:] = np.subtract(subtensor, center[j])
            subtensor[:] = np.divide(subtensor, max_value[j]-center[j])
            coord_scale.append(max_value[j]-center[j])
        scale.append(coord_scale)
    return scale
input_scale = np.asarray(norm_uniform(dataset,2)).squeeze()
output_scale = np.asarray(norm_uniform(groundtruth)).squeeze()
print(input_scale.shape, output_scale.shape)

(546, 2) (546,)


In [7]:
def normalize(tensor, coordinates=1):
    mean_value = [np.nanmean(tensor[:, :,i::coordinates]) for i in range(coordinates)]
    std_value = [np.nanstd(tensor[:, :,i::coordinates]) for i in range(coordinates)]
    for j in range(coordinates):
        subtensor = tensor[:, :, j::coordinates]
        subtensor[:] = np.subtract(subtensor, mean_value[j])
        subtensor[:] = np.divide(subtensor, std_value[j])
  
    return [(mean_value[i], std_value[i]) for i in range(coordinates)]

mom_x, mom_y = normalize(dataset, 2)
print(mom_x, mom_y)
mz, stdz = normalize(groundtruth)[0]

(-0.004493365406830015, 0.4484737458215585) (-0.5468003339046318, 0.47098643439052834)


In [8]:
# From python lists to pytorch tensors.
dataset = torch.tensor(np.nan_to_num(dataset), dtype=torch.float32)
groundtruth = torch.tensor(np.nan_to_num(groundtruth), dtype=torch.float32)
lengths = torch.tensor(lengths, dtype=torch.float32)
input_scale = torch.tensor(input_scale, dtype=torch.float32)
output_scale = torch.tensor(output_scale, dtype=torch.float32)

# Randomly shuffle videos
permutation = torch.randperm(dataset.size()[0])
dataset, groundtruth, lengths = dataset[permutation], groundtruth[permutation], lengths[permutation]
input_scale, output_scale = input_scale[permutation], output_scale[permutation]
print(dataset.shape, groundtruth.shape, lengths.shape)
print(input_scale.shape, output_scale.shape)

torch.Size([546, 16, 276]) torch.Size([546, 16, 138]) torch.Size([546])
torch.Size([546, 2]) torch.Size([546])


In [9]:
l1, l2 = len(dataset), len(groundtruth)
# Split in train, validation and test
training_kp, val_kp, test_kp = dataset[:round(0.74*l1)], dataset[round(0.74*l1):round(0.87*l1)], dataset[round(0.87*l1):]
training_lbl, val_lbl, test_lbl = groundtruth[:round(0.74*l2)], groundtruth[round(0.74*l2):round(0.87*l2)], groundtruth[round(0.87*l2):]
training_lengths, val_lengths, test_lengths = lengths[:round(0.74*l1)], lengths[round(0.74*l1):round(0.87*l1)], lengths[round(0.87*l1):]
training_inpscale, val_inpscale, test_inpscale = input_scale[:round(0.74*l1)], input_scale[round(0.74*l1):round(0.87*l1)], input_scale[round(0.87*l1):]
training_outscale, val_outscale, test_outscale = output_scale[:round(0.74*l1)], output_scale[round(0.74*l1):round(0.87*l1)], output_scale[round(0.87*l1):]

print(training_kp.shape, val_kp.shape, test_kp.shape)
print(training_lbl.shape, val_lbl.shape, test_lbl.shape)
print(training_lengths.shape, val_lengths.shape, test_lengths.shape)

torch.Size([404, 16, 276]) torch.Size([71, 16, 276]) torch.Size([71, 16, 276])
torch.Size([404, 16, 138]) torch.Size([71, 16, 138]) torch.Size([71, 16, 138])
torch.Size([404]) torch.Size([71]) torch.Size([71])


Finally we define the batch_size and put the datasets in DataLoaders.

In [10]:
train_data = TensorDataset(training_kp, training_lbl, training_lengths,
                          training_inpscale, training_outscale)
val_data = TensorDataset(val_kp, val_lbl, val_lengths,
                        val_inpscale, val_outscale)
test_data = TensorDataset(test_kp, test_lbl, test_lengths,
                         test_inpscale, test_outscale)

batch_size = 32

train_loader = DataLoader(train_data, shuffle=True, batch_size=batch_size, drop_last=True)
val_loader = DataLoader(val_data, shuffle=True, batch_size=batch_size, drop_last=True)
test_loader = DataLoader(test_data, shuffle=True, batch_size=batch_size, drop_last=True)

print(train_loader)

If we have a GPU available we set our device to GPU.

In [11]:
# torch.cuda.is_available() checks and returns a Boolean True if a GPU is available, else it'll return False
is_cuda = torch.cuda.is_available()

# If we have a GPU available, we'll set our device to GPU. We'll use this device variable later in our code.
if is_cuda:
    device = torch.device("cuda")
    print("GPU is available")
else:
    device = torch.device("cpu")
    print("GPU not available, CPU used")

GPU is available


Let's print some examples to see whether it is loaded correctly or not.

In [12]:
dataiter = iter(train_loader)
sample_x, sample_y, sample_len, iscale, oscale = dataiter.next()

print(sample_x.shape, sample_y.shape, sample_len.shape)

torch.Size([32, 16, 276]) torch.Size([32, 16, 138]) torch.Size([32])


## Model building
It is time to build the model for this approach. It will consist on a single/double layer LSTM followed by a Linear layer with output size the number of keypoints we want to estimate. I also define a method to initialize the hidden_state of the cell.

In [13]:
class LSTM_2D3D(nn.Module):
    
    def __init__(self, input_size, output_size, hidden_dim, n_layers, bidirectional, dropout=0.):
        super().__init__()
        # Save the model parameters
        self.output_size = output_size
        self.n_layers = n_layers
        self.hidden_dim = hidden_dim
        self.bi = bidirectional
        
        # Define the architecture
        self.lstm = nn.LSTM(input_size, hidden_dim, n_layers, batch_first=True, bidirectional=bidirectional, dropout=dropout)
        self.fc = nn.Sequential(
            nn.Dropout(0.5),
            nn.Linear(hidden_dim*(2 if self.bi else 1), output_size),
            nn.ReLU()
        )
        
    def forward(self, x, state, lengths):
        # Describe the forward step
        batch_size, seq_len = x.size(0), x.size(1) # We save the batch size and the (maximum) sequence length
        
        # Need to pack a tensor containing padded sequences of variable length
        packed = nn.utils.rnn.pack_padded_sequence(x, lengths=lengths, batch_first=True, enforce_sorted=False)
        ht, hidden_state = self.lstm(packed, state) # ht will be a PackedSequence

        # Need to flatten and reshape the output to feed it to the Linear layer
        ht = ht.data.contiguous() # ht will be of shape [sum(lengths), hidden_dim]
        ot = self.fc(ht) # ot will be of shape [sum(lengths), ouput_size]

        l_ot = [ot[:int(length)] for length in lengths] # list of batch elements, each shape [lengths[i], output_size]
        packed_ot = nn.utils.rnn.pack_sequence(l_ot, enforce_sorted=False) # PackedSequence
        # Finally return to shape [batch_size, seq_len, output_size]
        ot, _ = nn.utils.rnn.pad_packed_sequence(packed_ot, batch_first=True, total_length=seq_len)
        
        return ot, hidden_state
    
    def init_hidden(self, batch_size):
        weight = next(self.parameters()).data
        hidden = (weight.new(self.n_layers*(2 if self.bi else 1), batch_size, self.hidden_dim).zero_().to(device),
                      weight.new(self.n_layers*(2 if self.bi else 1), batch_size, self.hidden_dim).zero_().to(device))
        return hidden

In [14]:
# Define some model parameters
INPUT_SIZE = sample_x.size(2)
OUTPUT_SIZE = sample_y.size(2)
HIDDEN_DIM = 512
N_LAYERS = 2
BIDIRECTIONAL = False

# Instantiate the model
model = LSTM_2D3D(INPUT_SIZE, OUTPUT_SIZE, HIDDEN_DIM, N_LAYERS, BIDIRECTIONAL, dropout=0.7)
model.to(device)
print(model)
print(sum(p.numel() for p in model.parameters() if p.requires_grad))

LSTM_2D3D(
  (lstm): LSTM(276, 512, num_layers=2, batch_first=True, dropout=0.7)
  (fc): Sequential(
    (0): Dropout(p=0.5, inplace=False)
    (1): Linear(in_features=512, out_features=138, bias=True)
    (2): ReLU()
  )
)
3789962


## Training
Now we will proceed with the training. The first cell will define the learning rate, the loss function and the selected optimizer for the training process. Then we will proceed with a training over a number of epochs in which we will print it's training loss and validation loss. I also will be using Tensorboard to have a much nicer view of the results.

In [15]:
def substract_root_PJPE(output):
    jf = torch.chunk(output[:, :, :70], max_seq, dim=1)
    jhl, jhr = torch.chunk(output[:, :, 70:91], max_seq, dim=1), torch.chunk(output[:, :, 91:112], max_seq, dim=1)
    jb = torch.chunk(output[:, :, 112:], max_seq, dim=1)
    joints_merged = []
    roots = [33, 0, 0, 8]
    for i, joints in enumerate((jf, jhl, jhr, jb)):
        n_joints = []
        for chunk in joints:
            n_joints.append(chunk.sub(chunk[:,:,roots[i]].unsqueeze(2)))
        joints_merged.append(torch.cat(tuple(n_joints), dim=1))
    joints_merged = torch.cat(tuple(joints_merged), dim=2)
    return joints_merged

In [16]:
def mpjpe(rooted_o, rooted_l, seq_lens):
    MPJPE = []
    for i in range(len(seq_lens)):
        MPJPE.append(rooted_o[i,:int(seq_lens[i])].sub(rooted_l[i,:int(seq_lens[i])]).abs().mean().item())
    
    return np.mean(MPJPE)
    

In [17]:
NUM_EPOCHS = 60
lr = 1e-4
loss_function = nn.MSELoss()
one_cycle = True
optimizer = optim.Adam(model.parameters(), lr=lr)
if one_cycle:
    scheduler = torch.optim.lr_scheduler.OneCycleLR(optimizer, max_lr=lr, 
                                                  steps_per_epoch=len(train_loader), epochs=NUM_EPOCHS,
                                                  div_factor=20.0, final_div_factor=1000.0)

In [18]:
from datetime import datetime
name = 'lot_whole'
writer = SummaryWriter(log_dir=f'/deeplearning/logs/{name}{datetime.now()}_lr-{lr}_{NUM_EPOCHS}')

In [19]:
timer_beg = timer()

tr_losses = []
val_losses = []

model.train()
for i in range(NUM_EPOCHS):
    # Init the hidden state (ht, ct)
    h = model.init_hidden(batch_size)
    batch_losses = []
    train_MPJPE = []
    
    if i+1 == NUM_EPOCHS:
        preds, inps, labls, lens = [], [], [], []
        val_preds, val_inps, val_labls, val_lens = [], [], [], []
        iscale, oscale, val_iscale, val_oscale = [], [], [], []
        
    for inputs, labels, lengths, i_s, o_s in train_loader:
        h = tuple([e.data for e in h])
        inputs, labels, lengths = inputs.to(device), labels.to(device), lengths.to(device)
        # Clear the gradients
        optimizer.zero_grad()
        # Forward step
        output, h = model(inputs, h, lengths)
        
        if i+1 == NUM_EPOCHS:
            preds.append(output)
            inps.append(inputs)
            labls.append(labels)
            lens.append(lengths)
            iscale.append(i_s)
            oscale.append(o_s)

        # Loss calculation and backward step
        loss = loss_function(nn.utils.rnn.pack_padded_sequence(output, lengths=lengths, batch_first=True, 
                                                               enforce_sorted=False).data,
                             nn.utils.rnn.pack_padded_sequence(labels, lengths=lengths, batch_first=True,
                                                               enforce_sorted=False).data)
        loss.backward()
        # Weight update
        optimizer.step()
        # One cycle policy step
        if one_cycle:
            scheduler.step()
        
        # Output data collection for showing
        batch_losses.append(loss.item())
        rooted_o, rooted_l = substract_root_PJPE(output), substract_root_PJPE(labels)
        train_MPJPE.append(mpjpe(rooted_o, rooted_l, lengths))
    
    timer_end = timer()
    tr_losses.append(np.mean(batch_losses))
    writer.add_scalar('Loss/train', tr_losses[-1], i)   
    train_MPJPE_total = np.mean(train_MPJPE)
    
    # Validation at the end of an epoch
    val_h = model.init_hidden(batch_size)
    model.eval()
    val_loss = []
    val_MPJPE = []
    
    for inp, lab, lns, vis, vos in val_loader:
        val_h = tuple([each.data for each in val_h])
        inp, lab, lns = inp.to(device), lab.to(device), lns.to(device)
        out, val_h = model(inp, val_h, lns)
        
        if i+1 == NUM_EPOCHS:
            val_preds.append(output)
            val_inps.append(inp)
            val_labls.append(lab)
            val_lens.append(lns)
            val_iscale.append(vis)
            val_oscale.append(vos)
        
        loss = loss_function(nn.utils.rnn.pack_padded_sequence(out, lengths=lns, batch_first=True,
                                                               enforce_sorted=False).data,
                             nn.utils.rnn.pack_padded_sequence(lab, lengths=lns, batch_first=True,
                                                               enforce_sorted=False).data)
        val_loss.append(loss.item())
        rooted_o, rooted_l = substract_root_PJPE(out), substract_root_PJPE(lab)
        val_MPJPE.append(mpjpe(rooted_o, rooted_l, lns))
    
    val_losses.append(np.mean(val_loss))
    writer.add_scalar('Loss/validation', val_losses[-1], i)  
    val_MPJPE_total = np.mean(val_MPJPE)
    model.train()
    
    # Output loss and training time.
    print(f"Finished epoch {i+1}/{NUM_EPOCHS} in {(timer_end-timer_beg):.2f}s.\n",
             f"Loss: {np.mean(tr_losses[-1]):.4f}",
             f" Val Loss: {val_losses[-1]:.4f}\n"
             f"Train MPJPE: {train_MPJPE_total*stdz:.4f}", f" Val MPJPE: {val_MPJPE_total*stdz:.4f}")
    timer_beg = timer()

plt.figure()
plt.plot(tr_losses, label='train')
plt.plot(val_losses, label='validation')
plt.xlabel('Epoch')
plt.ylabel('MSELoss')
plt.legend()

Finished epoch 1/60 in 0.51s.
 Loss: 1.0021  Val Loss: 0.9388
Train MPJPE: 0.1850  Val MPJPE: 0.1837
Finished epoch 2/60 in 0.48s.
 Loss: 1.0016  Val Loss: 0.9304
Train MPJPE: 0.1844  Val MPJPE: 0.1811
Finished epoch 3/60 in 0.48s.
 Loss: 1.0066  Val Loss: 0.9300
Train MPJPE: 0.1828  Val MPJPE: 0.1828
Finished epoch 4/60 in 0.48s.
 Loss: 0.9977  Val Loss: 0.9416
Train MPJPE: 0.1834  Val MPJPE: 0.1812
Finished epoch 5/60 in 0.48s.
 Loss: 0.9846  Val Loss: 0.9104
Train MPJPE: 0.1821  Val MPJPE: 0.1826
Finished epoch 6/60 in 0.49s.
 Loss: 0.9735  Val Loss: 0.9055
Train MPJPE: 0.1812  Val MPJPE: 0.1826
Finished epoch 7/60 in 0.48s.
 Loss: 0.9554  Val Loss: 0.8852
Train MPJPE: 0.1787  Val MPJPE: 0.1778
Finished epoch 8/60 in 0.49s.
 Loss: 0.9129  Val Loss: 0.8238
Train MPJPE: 0.1747  Val MPJPE: 0.1727
Finished epoch 9/60 in 0.48s.
 Loss: 0.8511  Val Loss: 0.8271
Train MPJPE: 0.1648  Val MPJPE: 0.1587
Finished epoch 10/60 in 0.48s.
 Loss: 0.8362  Val Loss: 0.7697
Train MPJPE: 0.1520  Val MPJ

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Save the predictions for training and validation.

In [20]:
tr_predictions = torch.cat(tuple(preds), dim=0)
tr_inputs = torch.cat(tuple(inps), dim=0)
tr_groundtruth = torch.cat(tuple(labls), dim=0)
tr_lengths = torch.cat(tuple(lens), dim=0)
tr_inp_scale, tr_out_scale = torch.cat(tuple(iscale), dim=0), torch.cat(tuple(oscale), dim=0)

val_predictions = torch.cat(tuple(val_preds), dim=0)
val_inputs = torch.cat(tuple(val_inps), dim=0)
val_groundtruth = torch.cat(tuple(val_labls), dim=0)
val_length = torch.cat(tuple(val_lens), dim=0)
val_inp_scale, val_out_scale = torch.cat(tuple(val_iscale), dim=0), torch.cat(tuple(val_oscale), dim=0)

In [21]:
zeros = torch.zeros((138), device='cuda:0')

for i in range(len(tr_predictions)):
    count=0
    for frame in tr_predictions[i, :int(tr_lengths[i])]:
        if torch.all(frame.eq(zeros)):
            count +=1
    print(f'{count}/{int(tr_lengths[i])}')

0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16


In [22]:
zeros = torch.zeros((138), device='cuda:0')

for i in range(len(val_predictions)):
    count=0
    for frame in tr_predictions[i, :int(val_length[i])]:
        if torch.all(frame.eq(zeros)):
            count +=1
    print(f'{count}/{int(val_length[i])}')

0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16
0/16


In [23]:
print(stdz)

0.36032933866290445


In [24]:
torch.save(model.state_dict(), f'./{name}.pt')

In [25]:
model.load_state_dict(torch.load(f'./{name}.pt'))

<All keys matched successfully>

## Testing
After the training, we shall proceed with the performance test. This will go through the test batches and perform the inference, then it will show the test loss, as well as the performance metric. In this case, as we are working with human body keypoints, we will use the Mean Per Joint Position Error (MPJPE) metric, which outputs the mean euclidean distance between the joints (keypoints) positions estimated and the ones in the groundtruth.

The formula for MPJPE is the following:

$\text{MPJPE} = \frac1T\frac1N\displaystyle\sum_{t=1}^{T}\displaystyle\sum_{i=1}^{N}\|(J_{i}^{(t)}-J_{root}^{(t)})-(Ĵ_{i}^{(t)}-Ĵ_{root}^{(t)})\|$

Where N is the number of joints, and T the number of samples.

As we have seen in the formula above, we need to align the root joints of the labels and the network output. In order to do that, I have defined a function (`substract_root_PJPE`) that substracts the root joint of each keypoint set (face, hands, body) in the corresponding keypoint set.

In [26]:
test_losses = []
MPJPE = []
h = model.init_hidden(batch_size)
preds, inps, labls, lengs = [], [], [], []
iscal, oscal = [], []

model.eval()
for inputs_test, labels_test, lengths_test, is_test, os_test in test_loader:
    
    h = tuple([each.data for each in h])
    inputs_test, labels_test, lengths_test = inputs_test.to(device), labels_test.to(device), lengths_test.to(device)
    
    output_test, h = model(inputs_test, h, lengths_test)
    preds.append(output_test)
    inps.append(inputs_test)
    labls.append(labels_test)
    lengs.append(lengths_test)
    iscal.append(is_test)
    oscal.append(os_test)
    
    test_loss = loss_function(nn.utils.rnn.pack_padded_sequence(output_test, lengths=lengths_test, batch_first=True,
                                                               enforce_sorted=False).data,
                             nn.utils.rnn.pack_padded_sequence(labels_test, lengths=lengths_test, batch_first=True,
                                                               enforce_sorted=False).data)
    test_losses.append(test_loss.item())
    rooted_o, rooted_l = substract_root_PJPE(output_test), substract_root_PJPE(labels_test)
    MPJPE.append(mpjpe(rooted_o, rooted_l, lengths_test))

test_predictions = torch.cat(tuple(preds), dim=0)
test_inputs = torch.cat(tuple(inps), dim=0)
test_groundtruth = torch.cat(tuple(labls), dim=0)
test_inp_scale, test_out_scale = torch.cat(tuple(iscal), dim=0), torch.cat(tuple(oscal), dim=0)
MPJPE_total = np.mean(MPJPE)

In [27]:
print(f"MPJPE: {MPJPE_total*stdz:.4f}", f"\nTest loss: {np.mean(test_losses):.4f}")

MPJPE: 0.1369 
Test loss: 0.8719


### Save the results into a json

## Interpreation

Now to better understanding of the results, I will plot some of the frames from the last batches on the training and validation, and also from testing.

In [28]:
def plot_and_rotate(c_inputs, c_z, frames, frame):
    c_inputs[:,::2].mul_(mom_x[1])
    c_inputs[:,1::2].mul_(mom_y[1])
    c_z.mul_(stdz)

    bodiesXY = torch.chunk(c_inputs[frames, :], len(frames), dim=0)
    bodiesZ = torch.chunk(c_z[frames, :], len(frames), dim=0)
    
    x = bodiesXY[frame].squeeze()[::2]
    y = bodiesXY[frame].squeeze()[1::2]
    z = bodiesZ[frame].squeeze()
    
    r_eyebrow = [[c[i] for i in range(17, 22)] for c in [x,y,z]]
    l_eyebrow = [[c[i] for i in range(22, 27)] for c in [x,y,z]]
    l_eye = [[c[i] for i in range(42, 48)] for c in [x,y,z]]
    r_eye = [[c[i] for i in range(36, 42)] for c in [x,y,z]]
    nose1 = [[c[i] for i in range(27, 31)] for c in [x,y,z]]
    nose2 = [[c[i] for i in range(31, 36)] for c in [x,y,z]]
    ext_mouth = [[c[i] for i in range(48, 60)] for c in [x,y,z]]
    int_mouth = [[c[i] for i in range(60, 68)] for c in [x,y,z]]
    contour = [[c[i] for i in range(0, 17)] for c in [x,y,z]]
    
    l_arm = [[c[i+112] for i in [1, 0, 9, 10, 11]] for c in [x,y,z]]
    r_arm = [[c[i+112] for i in [0, 3, 4, 5]] for c in [x,y,z]]
    l_leg = [[c[i+112] for i in [0, 2, 12, 13, 14, 22, 23, 24]] for c in [x,y,z]]
    r_leg = [[c[i+112] for i in [2, 6, 7, 8, 19, 20, 21]] for c in [x,y,z]]
    head = [[c[i+112] for i in [18, 17, 1, 15, 16]] for c in [x,y,z]]

    rh0 = [[c[i+70] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]]
    rh1 = [[c[i+70] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]]
    rh2 = [[c[i+70] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]]
    rh3 = [[c[i+70] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]]
    rh4 = [[c[i+70] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]]
    lh0 = [[c[i+91] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]]
    lh1 = [[c[i+91] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]]
    lh2 = [[c[i+91] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]]
    lh3 = [[c[i+91] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]]
    lh4 = [[c[i+91] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]]
    
    fig = plt.figure()
    ax = fig.add_subplot(111, projection='3d')
    def init():
        ax.plot(r_eyebrow[0], r_eyebrow[2], r_eyebrow[1])
        ax.plot(l_eyebrow[0], l_eyebrow[2], l_eyebrow[1])
        ax.plot(l_eye[0], l_eye[2], l_eye[1])
        ax.plot(r_eye[0], r_eye[2], r_eye[1])
        ax.plot(nose1[0], nose1[2], nose1[1])
        ax.plot(nose2[0], nose2[2], nose2[1])
        ax.plot(ext_mouth[0], ext_mouth[2], ext_mouth[1])
        ax.plot(int_mouth[0], int_mouth[2], int_mouth[1])
        
        ax.plot(rh0[0], rh0[2], rh0[1])
        ax.plot(rh1[0], rh1[2], rh1[1])
        ax.plot(rh2[0], rh2[2], rh2[1])
        ax.plot(rh3[0], rh3[2], rh3[1])
        ax.plot(rh4[0], rh4[2], rh4[1])
        
        ax.plot(lh0[0], lh0[2], lh0[1])
        ax.plot(lh1[0], lh1[2], lh1[1])
        ax.plot(lh2[0], lh2[2], lh2[1])
        ax.plot(lh3[0], lh3[2], lh3[1])
        ax.plot(lh4[0], lh4[2], lh4[1])
        
        ax.plot(r_arm[0], r_arm[2], r_arm[1])
        ax.plot(l_arm[0], l_arm[2], l_arm[1])
        ax.plot(r_leg[0], r_leg[2], r_leg[1])
        ax.plot(l_leg[0], l_leg[2], l_leg[1])
        ax.plot(head[0], head[2], head[1])
        
        lims = ax.get_xlim(), ax.get_ylim(), ax.get_zlim()
        spans = lims[0][1]-lims[0][0], lims[1][1]-lims[1][0], lims[2][1]-lims[2][0]
        span = max(spans)
        margins = [(span-s)/2 for  s in spans]
        ax.set_xlim(lims[0][0]-margins[0], lims[0][1]+margins[0])
        ax.set_ylim(lims[1][0]-margins[1], lims[1][1]+margins[1])
        ax.set_zlim(lims[2][0]-margins[2], lims[2][1]+margins[2])
        

        return fig,

    def animate(i):
        ax.view_init(elev=220., azim=3.6*i)
        return fig,

    # Animate
    ani = animation.FuncAnimation(fig, animate, init_func=init,
                               frames=100, interval=100, blit=True)    

    return ani

In [29]:
def plot_frames(predictions, groundtruth, inputs, video_n, frames):
    
    inp = inputs.clone()
    preds = predictions.clone()
    grtr = groundtruth.clone()
    
    inp[:,:,::2].mul_(mom_x[1])
    inp[:,:,1::2].mul_(mom_y[1])
    preds.mul_(stdz)
    grtr.mul_(stdz)
    
    bodiesXY = torch.chunk(inp[video_n, frames, :], len(frames), dim=0)
    pred_bodiesZ = torch.chunk(preds[video_n, frames, :], len(frames), dim=0)
    true_bodiesZ = torch.chunk(grtr[video_n, frames, :], len(frames), dim=0)
   
    nrows = np.ceil(len(frames)/2)
    fig = plt.figure(figsize=(15, 6*nrows))
    fig2 = plt.figure(figsize=(15, 6*nrows))
    for frame in range(len(frames)):
        x = bodiesXY[frame].squeeze()[::2]
        y = bodiesXY[frame].squeeze()[1::2]
        pred_z = pred_bodiesZ[frame].squeeze()
        true_z = true_bodiesZ[frame].squeeze()
        
        r_eyebrow = tuple([[c[i] for i in range(17, 22)] for c in [x,y,z]] for z in [pred_z, true_z])
        l_eyebrow = tuple([[c[i] for i in range(22, 27)] for c in [x,y,z]] for z in [pred_z, true_z])
        l_eye = tuple([[c[i] for i in range(42, 48)] for c in [x,y,z]] for z in [pred_z, true_z])
        r_eye = tuple([[c[i] for i in range(36, 42)] for c in [x,y,z]] for z in [pred_z, true_z])
        nose1 = tuple([[c[i] for i in range(27, 31)] for c in [x,y,z]] for z in [pred_z, true_z])
        nose2 = tuple([[c[i] for i in range(31, 36)] for c in [x,y,z]] for z in [pred_z, true_z])
        ext_mouth = tuple([[c[i] for i in range(48, 60)] for c in [x,y,z]] for z in [pred_z, true_z])
        int_mouth = tuple([[c[i] for i in range(60, 68)] for c in [x,y,z]] for z in [pred_z, true_z])
        contour = tuple([[c[i] for i in range(0, 17)] for c in [x,y,z]] for z in [pred_z, true_z])
        
        rh0 = tuple([[c[i+70] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh1 = tuple([[c[i+70] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh2 = tuple([[c[i+70] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh3 = tuple([[c[i+70] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]] for z in [pred_z, true_z])
        rh4 = tuple([[c[i+70] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh0 = tuple([[c[i+91] for i in [0, 1, 2, 3, 4]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh1 = tuple([[c[i+91] for i in [0, 5, 6, 7, 8]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh2 = tuple([[c[i+91] for i in [0, 9, 10, 11, 12]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh3 = tuple([[c[i+91] for i in [0, 13, 14, 15, 16]] for c in [x,y,z]] for z in [pred_z, true_z])
        lh4 = tuple([[c[i+91] for i in [0, 17, 18, 19, 20]] for c in [x,y,z]] for z in [pred_z, true_z])
        
        r_arm = tuple([[c[i+112] for i in [1, 0, 9, 10, 11]] for c in [x,y,z]] for z in [pred_z, true_z])
        l_arm = tuple([[c[i+112] for i in [0, 3, 4, 5]] for c in [x,y,z]] for z in [pred_z, true_z])
        r_leg = tuple([[c[i+112] for i in [0, 2, 12, 13, 14, 22, 23, 24]] for c in [x,y,z]] for z in [pred_z, true_z])
        l_leg = tuple([[c[i+112] for i in [2, 6, 7, 8, 19, 20, 21]] for c in [x,y,z]] for z in [pred_z, true_z])
        head = tuple([[c[i+112] for i in [18, 17, 1, 15, 16]] for c in [x,y,z]] for z in [pred_z, true_z])

        ax = fig.add_subplot(nrows, 2, frame+1, projection='3d')
        ax.plot(r_eyebrow[0][0], r_eyebrow[0][1], r_eyebrow[0][2])
        ax.plot(l_eyebrow[0][0], l_eyebrow[0][1], l_eyebrow[0][2])
        ax.plot(l_eye[0][0], l_eye[0][1], l_eye[0][2])
        ax.plot(r_eye[0][0], r_eye[0][1], r_eye[0][2])
        ax.plot(nose1[0][0], nose1[0][1], nose1[0][2])
        ax.plot(nose2[0][0], nose2[0][1], nose2[0][2])
        ax.plot(ext_mouth[0][0], ext_mouth[0][1], ext_mouth[0][2])
        ax.plot(int_mouth[0][0], int_mouth[0][1], int_mouth[0][2])
        
        ax.plot(rh0[0][0], rh0[0][1], rh0[0][2])
        ax.plot(rh1[0][0], rh1[0][1], rh1[0][2])
        ax.plot(rh2[0][0], rh2[0][1], rh2[0][2])
        ax.plot(rh3[0][0], rh3[0][1], rh3[0][2])
        ax.plot(rh4[0][0], rh4[0][1], rh4[0][2])
        
        ax.plot(lh0[0][0], lh0[0][1], lh0[0][2])
        ax.plot(lh1[0][0], lh1[0][1], lh1[0][2])
        ax.plot(lh2[0][0], lh2[0][1], lh2[0][2])
        ax.plot(lh3[0][0], lh3[0][1], lh3[0][2])
        ax.plot(lh4[0][0], lh4[0][1], lh4[0][2])
        
        ax.plot(r_arm[0][0], r_arm[0][1], r_arm[0][2])
        ax.plot(l_arm[0][0], l_arm[0][1], l_arm[0][2])
        ax.plot(r_leg[0][0], r_leg[0][1], r_leg[0][2])
        ax.plot(l_leg[0][0], l_leg[0][1], l_leg[0][2])
        ax.plot(head[0][0], head[0][1], head[0][2])
        
        ax2 = fig2.add_subplot(nrows, 2, frame+1, projection='3d')
        ax2.plot(r_eyebrow[1][0], r_eyebrow[1][1], r_eyebrow[1][2])
        ax2.plot(l_eyebrow[1][0], l_eyebrow[1][1], l_eyebrow[1][2])
        ax2.plot(l_eye[1][0], l_eye[1][1], l_eye[1][2])
        ax2.plot(r_eye[1][0], r_eye[1][1], r_eye[1][2])
        ax2.plot(nose1[1][0], nose1[1][1], nose1[1][2])
        ax2.plot(nose2[1][0], nose2[1][1], nose2[1][2])
        ax2.plot(ext_mouth[1][0], ext_mouth[1][1], ext_mouth[1][2])
        ax2.plot(int_mouth[1][0], int_mouth[1][1], int_mouth[1][2])
        
        ax2.plot(rh0[1][0], rh0[1][1], rh0[1][2])
        ax2.plot(rh1[1][0], rh1[1][1], rh1[1][2])
        ax2.plot(rh2[1][0], rh2[1][1], rh2[1][2])
        ax2.plot(rh3[1][0], rh3[1][1], rh3[1][2])
        ax2.plot(rh4[1][0], rh4[1][1], rh4[1][2])
        
        ax2.plot(lh0[1][0], lh0[1][1], lh0[1][2])
        ax2.plot(lh1[1][0], lh1[1][1], lh1[1][2])
        ax2.plot(lh2[1][0], lh2[1][1], lh2[1][2])
        ax2.plot(lh3[1][0], lh3[1][1], lh3[1][2])
        ax2.plot(lh4[1][0], lh4[1][1], lh4[1][2])
        
        ax2.plot(r_arm[1][0], r_arm[1][1], r_arm[1][2])
        ax2.plot(l_arm[1][0], l_arm[1][1], l_arm[1][2])
        ax2.plot(r_leg[1][0], r_leg[1][1], r_leg[1][2])
        ax2.plot(l_leg[1][0], l_leg[1][1], l_leg[1][2])
        ax2.plot(head[1][0], head[1][1], head[1][2])
        
        lims = ax.get_xlim(), ax.get_ylim(), ax.get_zlim()
        spans = lims[0][1]-lims[0][0], lims[1][1]-lims[1][0], lims[2][1]-lims[2][0]
        span = max(spans)
        margins = [(span-s)/2 for  s in spans]
        ax.set_xlim(lims[0][0]-margins[0], lims[0][1]+margins[0])
        ax.set_ylim(lims[1][0]-margins[1], lims[1][1]+margins[1])
        ax.set_zlim(lims[2][0]-margins[2], lims[2][1]+margins[2])
        
        lims = ax2.get_xlim(), ax2.get_ylim(), ax2.get_zlim()
        spans = lims[0][1]-lims[0][0], lims[1][1]-lims[1][0], lims[2][1]-lims[2][0]
        span = max(spans)
        margins = [(span-s)/2 for  s in spans]
        ax2.set_xlim(lims[0][0]-margins[0], lims[0][1]+margins[0])
        ax2.set_ylim(lims[1][0]-margins[1], lims[1][1]+margins[1])
        ax2.set_zlim(lims[2][0]-margins[2], lims[2][1]+margins[2])

        ax.view_init(elev=-65., azim=-90.)
        ax2.view_init(elev=-65., azim=-90.)


### Single frame
On the first cell you can select which frames you want to plot and from which video of the batch. On the second you select which frame of the previosly selected you want to plot, specifying its index on the declared "frames" list.

In [30]:
# Last batches of training -output, inputs, labels-.
vid = 6
frames = [5]
    
c_inputs = tr_inputs[vid].clone()
c_output = tr_predictions[vid].clone()
c_labels = tr_groundtruth[vid].clone()

In [67]:
# Last batches of training -output, inputs, labels-.
vid = 1
frames = [100]

c_inputs = training_kp[vid].clone()
c_labels = training_lbl[vid].clone()
c_inputs[:,::2].mul_(training_inpscale[vid, 0])
c_inputs[:,1::2].mul_(training_inpscale[vid, 1])
c_labels.mul_(training_outscale[vid])

tensor([[ 37.1074,  50.2709,  46.0871,  ..., -50.1607, -46.5078,  51.9936],
        [ 39.6195,  50.7463,  46.2715,  ..., -50.3392, -46.0319,  51.9656],
        [ 37.4150,  44.4183,  46.4437,  ..., -50.9133, -46.3680,  51.3415],
        ...,
        [ 33.5482,  35.7709,  33.3052,  ..., -51.2048, -47.5370,  29.9741],
        [ 34.9311,  36.5086,  33.3370,  ..., -50.6932, -46.9213,  31.2541],
        [ 33.5324,  39.7177,  34.8118,  ..., -50.3689, -47.0373,  32.0275]])

In [31]:
HTML(plot_and_rotate(c_inputs, c_output, frames, 0).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [32]:
c_inputs = tr_inputs[vid].clone()
HTML(plot_and_rotate(c_inputs, c_labels, frames, 0).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

We repeat the same process for the last test batch.

In [31]:
# Last batches of test -output_test, inputs_test, labels_test-.
vid = 3
frames = [200, 3000]

c_inputs = test_inputs[vid].clone()
c_output = test_predictions[vid].clone()
c_labels = test_groundtruth[vid].clone()

In [32]:
HTML(plot_and_rotate(c_inputs, c_output, frames, 0).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [33]:
c_inputs = test_inputs[vid].clone()
HTML(plot_and_rotate(c_inputs, c_labels, frames, 0).to_html5_video())

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

### Slice of frames
Now let's plot a sequence of frames of the selected video. We will plot both the groundtruth and the predicted.

In [34]:
frames = [i for i in range(100,110)]
video_n = 6

In [35]:
plot_frames(tr_predictions, tr_groundtruth, tr_inputs, video_n, frames)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …